In [106]:
import xml.etree.ElementTree as ET
import re
from os import listdir
topic_files = listdir('./topics/')
for file in topic_files:
    file = './topics/' + file
# The regex used to capture the words segements
p_pattern = r'#id\((\w+\.\w\.\w+)\)\.{2}id\((\w+\.\w\.\w+)\)'
s_pattern = r'#id\((\w+\.\w\.\w+)\)'
two_pattern = r'#id\((\w+\.\w\.\w+?)(\d+)\)\.{2}id\((\w+\.\w\.\w+?)(\d+)\)'
one_pattern = r'#id\((\w+\.\w\.\w+?)(\d+)\)'
no_pattern = '\w+\.\w\.\w+?(\d+)'
name_space = {'nite':'http://nite.sourceforge.net/'}
words_pattern = '(.+?)words'

In [322]:
s = "ES2003b.B.words612"
re.match(words_pattern,s).group()

'ES2003b.B.words'

In [209]:
def parse_transcript(topic):
    topic_tree = ET.parse(topic)
    topic_root = topic_tree.getroot()
    topic_name = topic_root.attrib['{http://nite.sourceforge.net/}id']
    word_segments = []

    #get word segments without the paragraph bounds
    for child in topic_root.findall('.//topic//nite:child',name_space):
        try:
            word_segments.append(list(re.search(p_pattern,child.attrib['href']).groups()))
        except:
            word_segments.append(list(re.search(s_pattern,child.attrib['href']).groups()))
    #get topic bounds
    bounds = set()
    for topic in topic_root.findall('topic'):
        try:
            matched = re.search(p_pattern,topic.findall('.//nite:child[last()]',name_space)[-1].attrib['href'])
            bounds.add(matched.groups())
        except:
            matched = re.search(s_pattern,topic.findall('.//nite:child[last()]',name_space)[-1].attrib['href'])
            bounds.add(matched.groups())        
    #add topical bounds
    for seg in word_segments:
        if tuple(seg) in bounds:
            seg.append("**********")
    #get paragraph bounds
    seg_file_pattern1 = r'\w{7}\.\w\.'
    seg_file_pattern2 = r'\w{6}\.\w\.'
    wseg_with_parapgraph = []
    for seg in word_segments:
        if len(seg) == 1:
            wseg_with_parapgraph.append(seg)
        else:# the length of segment is 2 or 3, 3 means its a topical boundary
            try:
                file_name = re.match(seg_file_pattern1, seg[0]).group(0) + "segments.xml"
            except:
                file_name = re.match(seg_file_pattern2, seg[0]).group(0) + "segments.xml"
            tree =  ET.parse('./segments/'+file_name)
            root = tree.getroot()
            paras = []
            start = False
            for segment in root.findall('.//nite:child', name_space):
                if start:
                    try:
                        paras.append(','.join(re.search(p_pattern, segment.attrib['href']).groups()))
                    except:
                        paras.append(re.search(s_pattern, segment.attrib['href']).group(1))
                if seg[0] in segment.attrib['href']:
                    start = True
                    try:
                        paras.append(','.join(re.search(p_pattern, segment.attrib['href']).groups()))
                    except:
                        paras.append(re.search(s_pattern, segment.attrib['href']).group(1))
                if seg[1] in segment.attrib['href']:
                    break
            if len(paras) == 0:
                paras.append(seg[0] + ',' + seg[1])
            if seg[-1] == '**********':
                paras.append('**********')
            wseg_with_parapgraph.append(paras)
    return word_segments, wseg_with_parapgraph
    #start of writing txt process        
    with open('./txt_files/'+ topic_name+'.txt','w') as f:
        for e in wseg_with_parapgraph:
            for s in e:
                if s == '**********':
                    f.write(s + '\n')
                else:   
                    word_file = './words/'+ re.match(words_pattern,s).group() + '.xml'
                    tree = ET.parse(word_file)
                    root = tree.getroot()
                    sentence = s.split(',')
                    if len(sentence) == 1:# even single word sentence will be length of 2 here, 1 means vocal which can be dropped
                        try:
                            f.write(' ' + root.find('./w[@nite:id:"{}"]'.format(),name_space).text + '\n')
                        except:
                            pass
                    else:# length is 2, have start and end word
                        start = sentence[0]
                        end = sentence[1]
                        no_word = 0
                        begin = False
                        for word in root.findall('*'):
                            if begin:
                                if word.text:
                                    no_word += f.write(' ' + word.text) 
                                else:
                                    pass
                            if word.attrib['{http://nite.sourceforge.net/}id'] == start:
                                begin = True                               
                                if word.text:
                                    no_word = f.write(' ' + word.text) 
                                else:
                                    pass
                            if word.attrib['{http://nite.sourceforge.net/}id'] == end:      
                                if no_word:
                                    f.write('\n')
                                break

In [368]:
def parse_transcript(topic):
    topic_tree = ET.parse(topic)
    topic_root = topic_tree.getroot()
    topic_name = topic_root.attrib['{http://nite.sourceforge.net/}id']
    word_segments = []

    #get word segments without the paragraph bounds
    for child in topic_root.findall('.//topic//nite:child',name_space):
        try:
            word_segments.append(list(re.search(p_pattern,child.attrib['href']).groups()))
        except:
            word_segments.append(list(re.search(s_pattern,child.attrib['href']).groups()))
    #get topic bounds
    bounds = set()
    for topic in topic_root.findall('topic'):
        try:
            matched = re.search(p_pattern,topic.findall('.//nite:child[last()]',name_space)[-1].attrib['href'])
            bounds.add(matched.groups())
        except:
            matched = re.search(s_pattern,topic.findall('.//nite:child[last()]',name_space)[-1].attrib['href'])
            bounds.add(matched.groups())        
    #add topical bounds
    for seg in word_segments:
        if tuple(seg) in bounds:
            seg.append("**********")
    #get paragraph bounds
    seg_file_pattern1 = r'\w{7}\.\w\.'
    seg_file_pattern2 = r'\w{6}\.\w\.'
    wseg_with_parapgraph = []
    for seg in word_segments:
        if len(seg) == 1:
            wseg_with_parapgraph.append(seg)
        else:# the length of segment is 2 or 3, both 2 and 3 can indicate its a topical boundary
            try:
                file_name = re.match(seg_file_pattern1, seg[0]).group(0) + "segments.xml"
            except:
                file_name = re.match(seg_file_pattern2, seg[0]).group(0) + "segments.xml"
            tree =  ET.parse('./segments/'+file_name)
            root = tree.getroot()
            paras = []
            op_no = int(re.search(no_pattern,seg[0]).group(1))
            try:
                ed_no = int(re.search(no_pattern,seg[1]).group(1))#get start and end number of word in the seg
                for segment in root.findall('.//nite:child', name_space):#get paragraph bounds
                    if op_no > int(re.search(one_pattern,segment.attrib['href']).group(2)):
                        try:
                            #if the seg is totally in the segment
                            if ed_no < int(re.search(two_pattern,segment.attrib['href']).group(4)):
                                paras.append(seg[0] + ',' + seg[1])
                                break
                            elif ed_no > int(re.search(two_pattern,segment.attrib['href']).group(4)):#ed_no > end word_no of the segment
                                if op_no > int(re.search(two_pattern,segment.attrib['href']).group(4)):
                                    pass
                                elif op_no < int(re.search(two_pattern,segment.attrib['href']).group(4)):#op seg < end segment
                                    paras.append(seg[0] + ',' + re.search(p_pattern,segment.attrib['href']).group(2))
                                else:#end segment = op_no
                                    paras.append(seg[0])
                            else:#end_no = end segment
                                paras.append(seg[0] + ',' + seg[1])
                                break
                        except:# the segment contains only one word,don't include
                            pass
                    elif op_no == int(re.search(one_pattern,segment.attrib['href']).group(2)):
                        try:
                            if ed_no == int(re.search(two_pattern,segment.attrib['href']).group(4)):
                                paras.append(seg[0] + ',' + seg[1])
                                break                       
                            if ed_no > int(re.search(two_pattern,segment.attrib['href']).group(4)):#segment is totally in seg, add the whole segment
                                ##### need to create new boundaries fi FIRST Segment
                                #no = int(re.search(one_pattern,segment.attrib['href']).group(2)) - 1 
                                #paras.append(seg[0] + ','+re.search(one_pattern,segment.attrib['href']).group(1) + str(no))
                                #暂不考虑
                                paras.append(','.join(re.search(p_pattern, segment.attrib['href']).groups()))
                            else:#end_no < end_segemnt,so we can call an end for this iteration  
                                paras.append(seg[0] + ',' + seg[1])
                                break               
                        except:#only one word in the segment,and it equals op_no
                            paras.append(seg[0])
                    else:#op_no is < the op_segment,then 2 situations
                        try:
                            if ed_no <= int(re.search(two_pattern,segment.attrib['href']).group(4)):
                                paras.append(re.search(s_pattern,segment.attrib['href']).group(1) + ',' + seg[1])
                                break
                            else:#ed_no > end segment
                                paras.append(','.join(re.search(p_pattern, segment.attrib['href']).groups()))
                        except:#only one word and is between interval of seg, add
                            if int(re.search(one_pattern,segment.attrib['href']).group(2)) < ed_no:
                                paras.append(re.search(s_pattern,segment.attrib['href']).group(1))
                            elif int(re.search(one_pattern,segment.attrib['href']).group(2)) == ed_no:
                                paras.append(seg[1])
                                break
                #if len(paras) == 0:
                    #paras.append(seg[0] + ',' + seg[1])
                if seg[-1] == '**********':
                    paras.append('**********')
                wseg_with_parapgraph.append(paras)                
            except:#indicates that though of length 2, this seg is single plus "***"
                wseg_with_parapgraph.append(seg)
                
    #start of writing txt process        
    with open('./txt_files/'+ topic_name+'.txt','w') as f:
        for e in wseg_with_parapgraph:
            for s in e:
                if s == '**********':
                    f.write(s + '\n')
                else:   
                    word_file = './words/'+ re.match(words_pattern,s).group() + '.xml'
                    tree = ET.parse(word_file)
                    root = tree.getroot()
                    sentence = s.split(',')
                    if len(sentence) == 1:# even single word sentence will be length of 2 here, 1 may mean vocal which can be dropped
                        try:
                            f.write(' ' + root.find('./w[@nite:id="{}"]'.format(sentence[0]),name_space).text + '\n')
                        except:
                            pass
                    else:# length is 2, have start and end word
                        start = sentence[0]
                        end = sentence[1]
                        no_word = 0
                        begin = False
                        for word in root.findall('*'):
                            if begin:
                                if word.text:
                                    no_word += f.write(' ' + word.text) 
                                else:
                                    pass
                            if word.attrib['{http://nite.sourceforge.net/}id'] == start:
                                begin = True                               
                                if word.text:
                                    no_word = f.write(' ' + word.text) 
                                else:
                                    pass
                            if word.attrib['{http://nite.sourceforge.net/}id'] == end:      
                                if no_word:
                                    f.write('\n')
                                break

The copied previous main function

In [370]:
def parse_transcript(topic):
    topic_tree = ET.parse(topic)
    topic_root = topic_tree.getroot()
    topic_name = topic_root.attrib['{http://nite.sourceforge.net/}id']
    word_segments = []

    #get word segments without the paragraph bounds
    for child in topic_root.findall('.//topic//nite:child',name_space):
        try:
            word_segments.append(list(re.search(p_pattern,child.attrib['href']).groups()))
        except:
            word_segments.append(list(re.search(s_pattern,child.attrib['href']).groups()))
    #get topic bounds
    bounds = set()
    for topic in topic_root.findall('topic'):
        try:
            matched = re.search(p_pattern,topic.findall('.//nite:child[last()]',name_space)[-1].attrib['href'])
            bounds.add(matched.groups())
        except:
            matched = re.search(s_pattern,topic.findall('.//nite:child[last()]',name_space)[-1].attrib['href'])
            bounds.add(matched.groups())        
    #add topical bounds
    for seg in word_segments:
        if tuple(seg) in bounds:
            seg.append("**********")
    #get paragraph bounds
    seg_file_pattern1 = r'\w{7}\.\w\.'
    seg_file_pattern2 = r'\w{6}\.\w\.'
    wseg_with_parapgraph = []
    for seg in word_segments:
        if len(seg) == 1:
            wseg_with_parapgraph.append(seg)
        else:# the length of segment is 2 or 3, both 2 and 3 can indicate its a topical boundary
            try:
                file_name = re.match(seg_file_pattern1, seg[0]).group(0) + "segments.xml"
            except:
                file_name = re.match(seg_file_pattern2, seg[0]).group(0) + "segments.xml"
            tree =  ET.parse('./segments/'+file_name)
            root = tree.getroot()
            paras = []
            op_no = int(re.search(no_pattern,seg[0]).group(1))
            try:
                ed_no = int(re.search(no_pattern,seg[1]).group(1))#get start and end number of word in the seg
            except:#indicates that though of length 2, this seg is single plus "***"
                wseg_with_parapgraph.append(seg)
                #break
            for segment in root.findall('.//nite:child', name_space):#get paragraph bounds
                print(segment.attrib)
                if op_no > int(re.search(one_pattern,segment.attrib['href']).group(2)):
                    try:
                        #if the seg is totally in the segment
                        if ed_no < int(re.search(two_pattern,segment.attrib['href']).group(4)):
                            paras.append(seg[0] + ',' + seg[1])
                            break
                        elif ed_no > int(re.search(two_pattern,segment.attrib['href']).group(4)):#ed_no > end word_no of the segment
                            if op_no > int(re.search(two_pattern,segment.attrib['href']).group(4)):
                                pass
                            elif op_no < int(re.search(two_pattern,segment.attrib['href']).group(4)):#op seg < end segment
                                paras.append(seg[0] + ',' + re.search(p_pattern,segment.attrib['href']).group(2))
                            else:#end segment = op_no
                                paras.append(seg[0])
                        else:#end_no = end segment
                            paras.append(seg[0] + ',' + seg[1])
                            break
                    except:# the segment contains only one word,don't include
                        pass
                elif op_no == int(re.search(one_pattern,segment.attrib['href']).group(2)):
                    try:
                        if ed_no == int(re.search(two_pattern,segment.attrib['href']).group(4)):
                            paras.append(seg[0] + ',' + seg[1])
                            break                       
                        if ed_no > int(re.search(two_pattern,segment.attrib['href']).group(4)):#segment is totally in seg, add the whole segment
                            ##### need to create new boundaries fi FIRST Segment
                            #no = int(re.search(one_pattern,segment.attrib['href']).group(2)) - 1 
                            #paras.append(seg[0] + ','+re.search(one_pattern,segment.attrib['href']).group(1) + str(no))
                            #暂不考虑
                            paras.append(','.join(re.search(p_pattern, segment.attrib['href']).groups()))
                        else:#end_no < end_segemnt,so we can call an end for this iteration  
                            paras.append(seg[0] + ',' + seg[1])
                            break               
                    except:#only one word in the segment,and it equals op_no
                        paras.append(seg[0])
                else:#op_no is < the op_segment,then 2 situations
                    try:
                        if ed_no <= int(re.search(two_pattern,segment.attrib['href']).group(4)):
                            paras.append(re.search(s_pattern,segment.attrib['href']).group(1) + ',' + seg[1])
                            break
                        else:#ed_no > end segment
                            paras.append(','.join(re.search(p_pattern, segment.attrib['href']).groups()))
                    except:#only one word and is between interval of seg, add
                        if int(re.search(one_pattern,segment.attrib['href']).group(2)) < ed_no:
                            paras.append(re.search(s_pattern,segment.attrib['href']).group(1))
                        elif int(re.search(one_pattern,segment.attrib['href']).group(2)) == ed_no:
                            paras.append(seg[1])
                            break
            #if len(paras) == 0:
                #paras.append(seg[0] + ',' + seg[1])
            if seg[-1] == '**********':
                paras.append('**********')
            wseg_with_parapgraph.append(paras)
    return word_segments, wseg_with_parapgraph        
    #start of writing txt process        
    with open('./txt_files/'+ topic_name+'.txt','w') as f:
        for e in wseg_with_parapgraph:
            for s in e:
                if s == '**********':
                    f.write(s + '\n')
                else:   
                    word_file = './words/'+ re.match(words_pattern,s).group() + '.xml'
                    tree = ET.parse(word_file)
                    root = tree.getroot()
                    sentence = s.split(',')
                    if len(sentence) == 1:# even single word sentence will be length of 2 here, 1 may mean vocal which can be dropped
                        try:
                            f.write(' ' + root.find('./w[@nite:id="{}"]'.format(sentence[0]),name_space).text + '\n')
                        except:
                            pass
                    else:# length is 2, have start and end word
                        start = sentence[0]
                        end = sentence[1]
                        no_word = 0
                        begin = False
                        for word in root.findall('*'):
                            if begin:
                                if word.text:
                                    no_word += f.write(' ' + word.text) 
                                else:
                                    pass
                            if word.attrib['{http://nite.sourceforge.net/}id'] == start:
                                begin = True                               
                                if word.text:
                                    no_word = f.write(' ' + word.text) 
                                else:
                                    pass
                            if word.attrib['{http://nite.sourceforge.net/}id'] == end:      
                                if no_word:
                                    f.write('\n')
                                break

## The whole process

In [372]:
for file in topic_files:
    file = './topics/' + file
    parse_transcript(file)

{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words0)..id(IS1004b.A.words55)'}
{'href': 'IS1004b.B.words.xml#id(IS1004b.B.words0)..id(IS1004b.B.words1)'}
{'href': 'IS1004b.B.words.xml#id(IS1004b.B.words2)..id(IS1004b.B.words4)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words0)..id(IS1004b.A.words55)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words56)..id(IS1004b.A.words93)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words94)..id(IS1004b.A.words140)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words141)..id(IS1004b.A.words191)'}
{'href': 'IS1004b.C.words.xml#id(IS1004b.C.words0)'}
{'href': 'IS1004b.C.words.xml#id(IS1004b.C.words1)..id(IS1004b.C.words2)'}
{'href': 'IS1004b.C.words.xml#id(IS1004b.C.words3)..id(IS1004b.C.words6)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words0)..id(IS1004b.A.words55)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words56)..id(IS1004b.A.words93)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words94)..id(IS1004b.A.words140)'}
{'href': 'IS1004b.A.words.xml#

{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words301)..id(IS1004b.A.words303)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words304)..id(IS1004b.A.words306)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words307)..id(IS1004b.A.words314)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words315)..id(IS1004b.A.words316)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words317)..id(IS1004b.A.words323)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words324)..id(IS1004b.A.words328)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words329)..id(IS1004b.A.words330)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words331)..id(IS1004b.A.words334)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words335)..id(IS1004b.A.words336)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words337)..id(IS1004b.A.words338)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words339)..id(IS1004b.A.words346)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words347)..id(IS1004b.A.words351)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words352)

{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words727)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words728)..id(IS1004b.A.words734)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words735)..id(IS1004b.A.words737)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words738)..id(IS1004b.A.words739)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words740)..id(IS1004b.A.words742)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words743)..id(IS1004b.A.words747)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words748)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words749)..id(IS1004b.A.words755)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words756)..id(IS1004b.A.words757)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words758)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words759)..id(IS1004b.A.words760)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words761)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words762)..id(IS1004b.A.words770)'}
{'href': 'IS1004b.A.words.xml#id(IS1004b.A.words771)'}
{'href': 'IS10

{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words0)..id(IS1004b.D.words2)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words3)..id(IS1004b.D.words9)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words10)..id(IS1004b.D.words11)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words12)..id(IS1004b.D.words13)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words14)..id(IS1004b.D.words17)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words18)..id(IS1004b.D.words37)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words38)..id(IS1004b.D.words39)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words40)..id(IS1004b.D.words47)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words48)..id(IS1004b.D.words51)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words52)..id(IS1004b.D.words57)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words58)..id(IS1004b.D.words66)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words67)..id(IS1004b.D.words75)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words76)..id(IS1004b.D.words79)'}
{'h

{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words0)..id(IS1004b.D.words2)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words3)..id(IS1004b.D.words9)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words10)..id(IS1004b.D.words11)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words12)..id(IS1004b.D.words13)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words14)..id(IS1004b.D.words17)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words18)..id(IS1004b.D.words37)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words38)..id(IS1004b.D.words39)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words40)..id(IS1004b.D.words47)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words48)..id(IS1004b.D.words51)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words52)..id(IS1004b.D.words57)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words58)..id(IS1004b.D.words66)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words67)..id(IS1004b.D.words75)'}
{'href': 'IS1004b.D.words.xml#id(IS1004b.D.words76)..id(IS1004b.D.words79)'}
{'h

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'href': 'TS3003c.C.words.xml#id(TS3003c.C.words0)'}
{'href': 'TS3003c.C.words.xml#id(TS3003c.C.words1)..id(TS3003c.C.words2)'}
{'href': 'TS3003c.C.words.xml#id(TS3003c.C.words3)..id(TS3003c.C.words69)'}
{'href': 'TS3003c.C.words.xml#id(TS3003c.C.words70)..id(TS3003c.C.words112)'}
{'href': 'TS3003c.C.words.xml#id(TS3003c.C.words113)..id(TS3003c.C.words139)'}
{'href': 'TS3003c.C.words.xml#id(TS3003c.C.words140)..id(TS3003c.C.words176)'}
{'href': 'TS3003c.C.words.xml#id(TS3003c.C.words177)..id(TS3003c.C.words216)'}
{'href': 'TS3003c.C.words.xml#id(TS3003c.C.words217)..id(TS3003c.C.words285)'}
{'href': 'TS3003c.C.words.xml#id(TS3003c.C.words286)..id(TS3003c.C.words350)'}
{'href': 'TS3003c.C.words.xml#id(TS3003c.C.words351)..id(TS3003c.C.words366)'}
{'href': 'TS3003c.C.words.xml#id(TS3003c.C.words367)..id(TS3003c.C.words372)'}
{'href': 'TS3003c.C.words.xml#id(TS3003c.C.words373)..id(TS3003c.C.words374)'}
{'href': 'TS3003c.C.words.xml#id(TS3003c.C.words375)..id(TS3003c.C.words392)'}
{'href'

{'href': 'IB4003.A.words.xml#id(IB4003.A.words0)..id(IB4003.A.words64)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words65)..id(IB4003.A.words126)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words127)..id(IB4003.A.words332)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words333)..id(IB4003.A.words646)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words647)..id(IB4003.A.words700)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words701)..id(IB4003.A.words743)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words744)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words745)..id(IB4003.A.words751)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words752)..id(IB4003.A.words753)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words754)..id(IB4003.A.words769)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words770)..id(IB4003.A.words771)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words772)..id(IB4003.A.words804)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words805)..id(IB4003.A.words906)'}
{'href': 'IB4003.A.words.xml#id(IB4003.

{'href': 'IB4003.A.words.xml#id(IB4003.A.words0)..id(IB4003.A.words64)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words65)..id(IB4003.A.words126)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words127)..id(IB4003.A.words332)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words333)..id(IB4003.A.words646)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words647)..id(IB4003.A.words700)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words701)..id(IB4003.A.words743)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words744)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words745)..id(IB4003.A.words751)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words752)..id(IB4003.A.words753)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words754)..id(IB4003.A.words769)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words770)..id(IB4003.A.words771)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words772)..id(IB4003.A.words804)'}
{'href': 'IB4003.A.words.xml#id(IB4003.A.words805)..id(IB4003.A.words906)'}
{'href': 'IB4003.A.words.xml#id(IB4003.

KeyboardInterrupt: 

In [341]:
tree = ET.parse('./topics/IS1009a.topic.xml')
root = tree.getroot()
for child in root.findall('.//topic',name_space):
    print(child.attrib)


{'{http://nite.sourceforge.net/}id': 'IS1009a.topic.vkaraisk.1', 'other_description': 'introduction of participants and their roles'}
{'{http://nite.sourceforge.net/}id': 'IS1009a.topic.vkaraisk.2', 'other_description': 'project goal and design process'}
{'{http://nite.sourceforge.net/}id': 'IS1009a.topic.vkaraisk.3', 'other_description': 'drawing animals on the whiteboard'}
{'{http://nite.sourceforge.net/}id': 'IS1009a.topic.vkaraisk.4'}
{'{http://nite.sourceforge.net/}id': 'IS1009a.topic.vkaraisk.5', 'other_description': 'ideas about remote control design'}
{'{http://nite.sourceforge.net/}id': 'IS1009a.topic.vkaraisk.7', 'other_description': 'size and functionality'}
{'{http://nite.sourceforge.net/}id': 'IS1009a.topic.vkaraisk.8', 'other_description': 'how it looks'}
{'{http://nite.sourceforge.net/}id': 'IS1009a.topic.vkaraisk.9', 'other_description': 'how to find when it is misplaced'}
{'{http://nite.sourceforge.net/}id': 'IS1009a.topic.vkaraisk.6'}


### !!! Runing time is excessively long, better reduce iteration to optimize the running efficiency

## To be done
### ??? Why some segment iteration breaks too early
### <= and >= is not adequate, we need to split the < and =
## OR add end compare with start

In [333]:
tree = ET.parse('./words/ES2003b.B.words.xml')
root = tree.getroot()
print(root.find('./w[@nite:id="{}"]'.format('ES2003b.B.words612'),name_space).text)

Um


In [369]:
#test the parsing process on one transcript
parse_transcript('./topics/IS1009a.topic.xml')

In [366]:
a

[['IS1009a.A.words0', 'IS1009a.A.words15'],
 ['IS1009a.D.words0', 'IS1009a.D.words1'],
 ['IS1009a.C.words0', 'IS1009a.C.words1'],
 ['IS1009a.D.words2', 'IS1009a.D.words12'],
 ['IS1009a.A.words16', 'IS1009a.A.words31'],
 ['IS1009a.B.words0', 'IS1009a.B.words39'],
 ['IS1009a.A.words32', 'IS1009a.A.words37'],
 ['IS1009a.D.words13', 'IS1009a.D.words27'],
 ['IS1009a.A.words38', 'IS1009a.A.words44'],
 ['IS1009a.D.words28', 'IS1009a.D.words32'],
 ['IS1009a.A.words45', 'IS1009a.A.words46'],
 ['IS1009a.C.words2', 'IS1009a.C.words39'],
 ['IS1009a.A.words47', 'IS1009a.A.words85'],
 ['IS1009a.D.words33', 'IS1009a.D.words34', '**********'],
 ['IS1009a.A.words86', 'IS1009a.A.words128'],
 ['IS1009a.D.words35', 'IS1009a.D.words36'],
 ['IS1009a.A.words129', 'IS1009a.A.words173'],
 ['IS1009a.D.words37', 'IS1009a.D.words38'],
 ['IS1009a.A.words174', 'IS1009a.A.words211'],
 ['IS1009a.D.words39', 'IS1009a.D.words42'],
 ['IS1009a.A.words212', 'IS1009a.A.words221'],
 ['IS1009a.D.words43', 'IS1009a.D.words44'

In [367]:
b

[['IS1009a.A.words0,IS1009a.A.words15'],
 ['IS1009a.D.words0,IS1009a.D.words1'],
 ['IS1009a.C.words0,IS1009a.C.words1'],
 ['IS1009a.D.words2,IS1009a.D.words5', 'IS1009a.D.words6,IS1009a.D.words12'],
 ['IS1009a.A.words16,IS1009a.A.words31'],
 ['IS1009a.B.words0,IS1009a.B.words39'],
 ['IS1009a.A.words32,IS1009a.A.words33',
  'IS1009a.A.words34,IS1009a.A.words37'],
 ['IS1009a.D.words13,IS1009a.D.words27'],
 ['IS1009a.A.words38,IS1009a.A.words44'],
 ['IS1009a.D.words28,IS1009a.D.words32'],
 ['IS1009a.A.words45,IS1009a.A.words46'],
 ['IS1009a.C.words2,IS1009a.C.words39'],
 ['IS1009a.A.words47,IS1009a.A.words85'],
 ['IS1009a.D.words33,IS1009a.D.words34', '**********'],
 ['IS1009a.A.words86,IS1009a.A.words88',
  'IS1009a.A.words89,IS1009a.A.words128'],
 ['IS1009a.D.words35,IS1009a.D.words36'],
 ['IS1009a.A.words129,IS1009a.A.words173'],
 ['IS1009a.D.words37,IS1009a.D.words38'],
 ['IS1009a.A.words174,IS1009a.A.words211'],
 ['IS1009a.D.words39,IS1009a.D.words40',
  'IS1009a.D.words41',
  'IS100

In [246]:
if None:
    pass
else:
    print('a')

a


In [315]:
'ES2003b.B.words612'.split(',')[0]

'ES2003b.B.words612'

re.match(words_pattern,'ES2002a.B.words0,ES2002a.B.words1').group()

In [211]:
tree = ET.parse('./words/ES2002a.B.words.xml')
root = tree.getroot()
for word in root.findall('*'):
    if word.attrib['{http://nite.sourceforge.net/}id'] == 'ES2002a.B.words4':
        print(word.text)

None


['ES2002a.B.words275']

ES2002a.B.words0,ES2002a.B.words1

In [82]:
bounds

{('ES2002d.B.words0', 'ES2002d.B.words170'),
 ('ES2002d.B.words1612', 'ES2002d.B.words1613'),
 ('ES2002d.B.words2586', 'ES2002d.B.words2589'),
 ('ES2002d.B.words2873', 'ES2002d.B.words2885'),
 ('ES2002d.B.words446', 'ES2002d.B.words473')}

In [83]:
for seg in word_segments:
    if tuple(seg) in bounds:
        seg.append("**********")

In [32]:
def a(topic):
    topic_tree = ET.parse(topic)
    topic_root = topic_tree.getroot()
    topic_name = topic_root.attrib['{http://nite.sourceforge.net/}id']
    word_segments = []

    #get word segments without the paragraph bounds
    for topic in topic_root.iter('topic'):
        for child in topic.findall('nite:child',name_space):
            try:
                word_segments.append(list(re.search(p_pattern,child.attrib['href']).groups()))
            except:
                word_segments.append(list(re.search(s_pattern,child.attrib['href']).groups()))
    #get topic bounds
    bounds = set()
    for topic in topic_root.findall('topic'):
        try:
            matched = re.search(p_pattern,topic.findall('.//nite:child[last()]',name_space)[-1].attrib['href'])
            bounds.add(matched.groups())
        except:
            matched = re.search(s_pattern,topic.findall('.//nite:child[last()]',name_space)[-1].attrib['href'])
            bounds.add(matched.groups())        
    #add topical bounds
    for seg in word_segments:
        if tuple(seg) in bounds:
            seg.append("**********")
    #get paragraph bounds
    seg_file_pattern1 = r'\w{7}\.\w\.'
    seg_file_pattern2 = r'\w{6}\.\w\.'
    wseg_with_parapgraph = []
    for seg in word_segments:
        if len(seg) == 1:
            wseg_with_parapgraph.append(seg)
        else:# the length of segment is 2 or 3, 3 means its a topical boundary
            try:
                file_name = re.match(seg_file_pattern1, seg[0]).group(0) + "segments.xml"
            except:
                file_name = re.match(seg_file_pattern2, seg[0]).group(0) + "segments.xml"
            tree =  ET.parse('./segments/'+file_name)
            root = tree.getroot()
            paras = []
            start = False
            for segment in root.findall('.//nite:child', name_space):
                if start:
                    try:
                        paras.append(','.join(re.search(p_pattern, segment.attrib['href']).groups()))
                    except:
                        paras.append(re.search(s_pattern, segment.attrib['href']).group(1))
                if seg[0] in segment.attrib['href']:
                    start = True
                    try:
                        paras.append(','.join(re.search(p_pattern, segment.attrib['href']).groups()))
                    except:
                        paras.append(re.search(s_pattern, segment.attrib['href']).group(1))
                if seg[1] in segment.attrib['href']:
                    break
            if len(paras) == 0:
                print(seg)
                print(segment.attrib)
                paras.append(seg[0] + ',' + seg[1])
            if seg[-1] == '**********':
                paras.append('**********')
            wseg_with_parapgraph.append(paras)

In [44]:
a('./topics/ES2003b.topic.xml')

['ES2003b.B.words127', 'ES2003b.B.words159']
{'href': 'ES2003b.B.words.xml#id(ES2003b.B.words70)..id(ES2003b.B.words159)'}
['ES2003b.B.words281', 'ES2003b.B.words320']
{'href': 'ES2003b.B.words.xml#id(ES2003b.B.words160)..id(ES2003b.B.words320)'}
['ES2003b.B.words415', 'ES2003b.B.words449']
{'href': 'ES2003b.B.words.xml#id(ES2003b.B.words417)..id(ES2003b.B.words449)'}
['ES2003b.B.words581', 'ES2003b.B.words611']
{'href': 'ES2003b.B.words.xml#id(ES2003b.B.words2608)..id(ES2003b.B.words2621)'}
['ES2003b.B.words949', 'ES2003b.B.words954']
{'href': 'ES2003b.B.words.xml#id(ES2003b.B.words919)..id(ES2003b.B.words954)'}
['ES2003b.B.words1985', 'ES2003b.B.words2003']
{'href': 'ES2003b.B.words.xml#id(ES2003b.B.words1972)..id(ES2003b.B.words2003)'}
['ES2003b.B.words1622', 'ES2003b.B.words1719']
{'href': 'ES2003b.B.words.xml#id(ES2003b.B.words1548)..id(ES2003b.B.words1719)'}
['ES2003b.B.words1484', 'ES2003b.B.words1524']
{'href': 'ES2003b.B.words.xml#id(ES2003b.B.words1453)..id(ES2003b.B.words152

In [1]:
with open('./test.txt','w') as f:
    a = f.write('')
    a += f.write(' ')
    a += f.write('')
    print(a)

1


In [84]:
#now we know where the topical boundaries are
word_segments

[['ES2002d.B.words0', 'ES2002d.B.words170', '**********'],
 ['ES2002d.A.words0', 'ES2002d.A.words1'],
 ['ES2002d.D.words0', 'ES2002d.D.words86'],
 ['ES2002d.A.words2', 'ES2002d.A.words9'],
 ['ES2002d.B.words171', 'ES2002d.B.words176'],
 ['ES2002d.D.words87', 'ES2002d.D.words107'],
 ['ES2002d.C.words0', 'ES2002d.C.words2'],
 ['ES2002d.A.words10', 'ES2002d.A.words46'],
 ['ES2002d.C.words3', 'ES2002d.C.words6'],
 ['ES2002d.A.words47', 'ES2002d.A.words59'],
 ['ES2002d.C.words7', 'ES2002d.C.words12'],
 ['ES2002d.B.words177', 'ES2002d.B.words187'],
 ['ES2002d.D.words108'],
 ['ES2002d.A.words60', 'ES2002d.A.words132'],
 ['ES2002d.C.words13', 'ES2002d.C.words18'],
 ['ES2002d.B.words188', 'ES2002d.B.words192'],
 ['ES2002d.C.words19', 'ES2002d.C.words22'],
 ['ES2002d.A.words133', 'ES2002d.A.words164'],
 ['ES2002d.C.words23', 'ES2002d.C.words32'],
 ['ES2002d.B.words193', 'ES2002d.B.words198'],
 ['ES2002d.A.words165', 'ES2002d.A.words169'],
 ['ES2002d.C.words33', 'ES2002d.C.words43'],
 ['ES2002d.B

### ---- A test of how to capture paragraph boundaries

In [85]:
tree = ET.parse('./segments/ES2002b.B.segments.xml')
root = tree.getroot()

In [86]:
para = []
start = False
for segment in root.findall('.//nite:child', name_space):
    if start:
        para.append(re.search(p_pattern, segment.attrib['href']).groups())
    if 'ES2002b.B.words0' in segment.attrib['href']:
        para.append(re.search(p_pattern, segment.attrib['href']).groups())
        start = True
    if 'ES2002b.B.words128' in segment.attrib['href']:
        break

In [87]:
para

[('ES2002b.B.words0', 'ES2002b.B.words4'),
 ('ES2002b.B.words5', 'ES2002b.B.words7'),
 ('ES2002b.B.words8', 'ES2002b.B.words9'),
 ('ES2002b.B.words10', 'ES2002b.B.words128')]

In [88]:
'ES2002b.B.words0' in "ES2002b.B.words.xml#id(ES2002b.B.words0)..id(ES2002b.B.words4)"

True

### Then we need to figure out paragraph bounds

### First we try to get the complete transcript for one topic xml file -- "`ES2002b.topic.xml`"

In [89]:
seg_file_pattern = r'\w{7}\.\w\.'

### Some more complicated situation that we need to be able to  address:
**1. The start word of a segment from the topic file(`length 2`) is in the interval of segment in segments files, the end word matches the one in the segments file**

**2. Start word matches but the end word falls in the interval**
3. Both start word and end word are in the interval
4. The segment in segments is single length and match only the start word of a segment in topic file
5. The segment in segments is single length and match only the end word of a segment in topic file

### It's much easier to deal with the stareting and ending intervals in only numeric mode

                try:
                    paras.append(','.join(re.search(p_pattern, segment.attrib['href']).groups()))
                except:
                    paras.append(re.search(s_pattern, segment.attrib['href']).group(1))

In [116]:
wseg_with_parapgraph1 = []
for seg in word_segments:
    if len(seg) == 1:
        wseg_with_parapgraph1.append(seg)
    else:# the length of segment is 2 or 3, 3 means its a topical boundary
        file_name = re.match(seg_file_pattern, seg[0]).group(0) + "segments.xml"
        tree =  ET.parse('./segments/'+file_name)
        root = tree.getroot()
        paras = []
        start = False
        for segment in root.findall('.//nite:child', name_space):
            if start:
                try:
                    paras.append(','.join(re.search(p_pattern, segment.attrib['href']).groups()))
                except:
                    paras.append(re.search(s_pattern, segment.attrib['href']).group(1))
            if seg[0] in segment.attrib['href']:
                start = True
                try:
                    paras.append(','.join(re.search(p_pattern, segment.attrib['href']).groups()))
                except:
                    paras.append(re.search(s_pattern, segment.attrib['href']).group(1))
            if seg[1] in segment.attrib['href']:
                break
        if len(paras) == 0:
            paras.append(seg[0] + ',' + seg[1])
        if seg[-1] == '**********':
            paras.append('**********')
        wseg_with_parapgraph1.append(paras)        

['ES2002d.B.words474', 'ES2002d.B.words502']
{'href': 'ES2002d.B.words.xml#id(ES2002d.B.words490)..id(ES2002d.B.words502)'}
['ES2002d.B.words742', 'ES2002d.B.words767']
{'href': 'ES2002d.B.words.xml#id(ES2002d.B.words720)..id(ES2002d.B.words767)'}
['ES2002d.B.words1614', 'ES2002d.B.words1632']
{'href': 'ES2002d.B.words.xml#id(ES2002d.B.words1612)..id(ES2002d.B.words1632)'}
['ES2002d.B.words1695', 'ES2002d.B.words1710']
{'href': 'ES2002d.B.words.xml#id(ES2002d.B.words1685)..id(ES2002d.B.words1710)'}
['ES2002d.B.words1913', 'ES2002d.B.words1917']
{'href': 'ES2002d.B.words.xml#id(ES2002d.B.words1910)..id(ES2002d.B.words1917)'}
['ES2002d.B.words2088', 'ES2002d.B.words2127']
{'href': 'ES2002d.B.words.xml#id(ES2002d.B.words2076)..id(ES2002d.B.words2127)'}
['ES2002d.B.words2590', 'ES2002d.B.words2645']
{'href': 'ES2002d.B.words.xml#id(ES2002d.B.words2586)..id(ES2002d.B.words2645)'}


# REVISED VERSION TO DEAL WITH SEGMENTS SPLIT IN TWO SUBTOPICS
wseg_with_parapgraph = []
for seg in word_segments:
    if len(seg) == 1:
        wseg_with_parapgraph.append(seg)
    else:# the length of segment is 2 or 3, 3 means its a topical boundary
        file_name = re.match(seg_file_pattern, seg[0]).group(0) + "segments.xml"
        tree =  ET.parse('./segments/'+file_name)
        root = tree.getroot()
        paras = []
        #start = False
        for segment in root.findall('.//nite:child', name_space):
            #if start:
                #try:
                    #paras.append(','.join(re.search(p_pattern, segment.attrib['href']).groups()))
                #except:
                    #paras.append(re.search(s_pattern, segment.attrib['href']).group(1))
            if re.search(p_pattern, segment.attrib['href']):#this means the segment has length of 2
                if seg[0] >= re.search(p_pattern, segment.attrib['href']).group(1) and seg[1] >= re.search(p_pattern, segment.attrib['href']).group(2):
                    paras.append(seg[0] + ',' + re.search(p_pattern, segment.attrib['href']).group(2))                   
                if seg[0] >= re.search(p_pattern, segment.attrib['href']).group(1) and seg[1] < re.search(p_pattern, segment.attrib['href']).group(2):
                    paras.append(seg[0] + ',' + seg[1])  
                if seg[0] < re.search(p_pattern, segment.attrib['href']).group(1) and seg[1] >= re.search(p_pattern, segment.attrib['href']).group(2):
        if seg[-1] == '**********':
            paras.append('**********')
        if len(paras) == 0:
            print(seg)
            print(segment.attrib)
        wseg_with_parapgraph.append(paras)

                start = True
                try:
                    paras.append(re.search(p_pattern, segment.attrib['href']).group(1) + ',' + seg[0])
                except:
                    paras.append(seg[0])
            try:    
                if seg[1] <= re.search(p_pattern, segment.attrib['href']).group(2):
                    break
            except:
                if seg[1] <= re.search(s_pattern, segment.attrib['href']).group(1):
                    break

In [91]:
re.match('\w+','abc').group(0)

'abc'

In [92]:
wseg_with_parapgraph1

[['ES2002d.B.words0,ES2002d.B.words80',
  'ES2002d.B.words81,ES2002d.B.words170',
  '**********'],
 ['ES2002d.A.words0,ES2002d.A.words1'],
 ['ES2002d.D.words0,ES2002d.D.words86'],
 ['ES2002d.A.words2,ES2002d.A.words9'],
 ['ES2002d.B.words171,ES2002d.B.words172',
  'ES2002d.B.words173,ES2002d.B.words174',
  'ES2002d.B.words175,ES2002d.B.words176'],
 ['ES2002d.D.words87,ES2002d.D.words107'],
 ['ES2002d.C.words0,ES2002d.C.words2'],
 ['ES2002d.A.words10,ES2002d.A.words46'],
 ['ES2002d.C.words3,ES2002d.C.words6'],
 ['ES2002d.A.words47,ES2002d.A.words59'],
 ['ES2002d.C.words7,ES2002d.C.words12'],
 ['ES2002d.B.words177,ES2002d.B.words187'],
 ['ES2002d.D.words108'],
 ['ES2002d.A.words60,ES2002d.A.words132'],
 ['ES2002d.C.words13,ES2002d.C.words14',
  'ES2002d.C.words15,ES2002d.C.words16',
  'ES2002d.C.words17,ES2002d.C.words18'],
 ['ES2002d.B.words188,ES2002d.B.words192'],
 ['ES2002d.C.words19,ES2002d.C.words22'],
 ['ES2002d.A.words133,ES2002d.A.words164'],
 ['ES2002d.C.words23,ES2002d.C.words

In [111]:
with open('./txt_files/'+ topic_name+'.txt','w') as f:
    for e in wseg_with_parapgraph1:
        for s in e:
            f.write(s + '\n')

### ------- a break line for automating all files----

In [17]:
from os import listdir
topic_files = listdir('./topics/')
seg_files = listdir('./segments/')
words_files = listdir('./words/')

In [371]:
len(listdir('./txt_files/'))

140

In [119]:
with open('./test.txt','w') as f:
    for e in [[],'1','2']:
         for s in e:
            f.write(s+'\n')